
# Advanced mixture of experts


In [ ]:
from __future__ import annotations

from gemseo import create_benchmark_dataset
from gemseo.mlearning import create_regression_model
from gemseo.mlearning.quality_measures.f1_measure import F1Measure
from gemseo.mlearning.quality_measures.mse_measure import MSEMeasure
from gemseo.mlearning.quality_measures.silhouette_measure import SilhouetteMeasure

In this example,
we seek to estimate the Rosenbrock function from the :class:`.RosenbrockDataset`.



In [ ]:
dataset = create_benchmark_dataset("RosenbrockDataset", opt_naming=False)

For that purpose,
we will use a :class:`.MOERegressor` in an advanced way:
we will not set the clustering, classification and regression algorithms
but select them according to their performance
from several candidates that we will provide.
Moreover,
for a given candidate,
we will propose several settings,
compare their performances
and select the best one.

## Initialization
First,
we initialize a :class:`.MOERegressor` with soft classification
by means of the high-level machine learning function :func:`.create_regression_model`.



In [ ]:
model = create_regression_model("MOERegressor", dataset, hard=False)

## Clustering
Then,
we add two clustering algorithms
with different numbers of clusters (called *components* for the Gaussian Mixture)
and set the :class:`.SilhouetteMeasure` as clustering measure
to be evaluated from the learning set.
During the learning stage,
the mixture of experts will select the clustering algorithm
and the number of clusters
minimizing this measure.



In [ ]:
model.set_clustering_measure(SilhouetteMeasure)
model.add_clusterer_candidate("KMeans", n_clusters=[2, 3, 4])
model.add_clusterer_candidate("GaussianMixture", n_components=[3, 4, 5])

## Classification
We also add classification algorithms
with different settings
and set the :class:`.F1Measure` as classification measure
to be evaluated from the learning set.
During the learning stage,
the mixture of experts will select the classification algorithm and the settings
minimizing this measure.



In [ ]:
model.set_classification_measure(F1Measure)
model.add_classifier_candidate("KNNClassifier", n_neighbors=[3, 4, 5])
model.add_classifier_candidate("RandomForestClassifier", n_estimators=[100])

## Regression
We also add regression algorithms
and set the :class:`.MSEMeasure` as regression measure
to be evaluated from the learning set.
During the learning stage, for each cluster,
the mixture of experts will select the regression algorithm minimizing this measure.



In [ ]:
model.set_regression_measure(MSEMeasure)
model.add_regressor_candidate("LinearRegressor")
model.add_regressor_candidate("RBFRegressor")

<div class="alert alert-info"><h4>Note</h4><p>We could also add candidates for some learning stages,
   e.g. clustering and regression,
   and set the machine learning algorithms for the remaining ones,
   e.g. classification.</p></div>

## Training
Lastly,
we learn the data
and select the best machine learning algorithm
for both clustering, classification and regression steps.



In [ ]:
model.learn()

## Result
We can get information on this model,
on the sub-machine learning models selected among the candidates
and on their selected settings.
We can see that
a :class:`.KMeans` with four clusters has been selected for the clustering stage,
as well as a :class:`.RandomForestClassifier` for the classification stage
and a :class:`.RBFRegressor` for each cluster.



In [ ]:
print(model)

<div class="alert alert-info"><h4>Note</h4><p>By adding candidates,
   and depending on the complexity of the function to be approximated,
   one could obtain different regression models according to the clusters.
   For example,
   one could use a :class:`.PolynomialRegressor` with order 2
   on a sub-part of the input space
   and a :class:`.GaussianProcessRegressor`
   on another sub-part of the input space.</p></div>

Once built,
this mixture of experts can be used as any :class:`.MLRegressionAlgo`.

.. seealso::

   `Another example <sphx_glr_examples_mlearning_regression_model_plot_moe.py>`
   proposes a standard use of :class:`.MOERegressor`.

